#### Dependencies

In [1]:
#!pip install numpy pandas requests scipy pydendroheatmap matplotlib
import pandas as pd
import numpy as np
import requests
from collections import defaultdict
import re
import json
import matplotlib
import pydendroheatmap as pdh
import scipy.cluster.hierarchy as sch
import scipy.spatial.distance as ssd

#### Config

In [2]:
awatch = {'polls': "https://www.abgeordnetenwatch.de/api/v2/polls?field_legislature=%(legislature)d&range_start=%(range_start)d&range_end=%(range_end)d",
         'votes': "https://www.abgeordnetenwatch.de/api/v2/votes?poll=%(poll)d&range_start=%(range_start)d&range_end=%(range_end)d",
        }

legis_id = 83
legis_name = {111: "Bundestag 2017-2021", 97: "Bundestag 2013-2017", 83: "Bundestag 2009-2013"}

#matplotlib.rcParams['figure.dpi'] = 300
#matplotlib.rcParams['figure.figsize'] = (16,9)

g_votes = {}

#### Functions

In [3]:
def from_url(url, max_range=float("inf"), **kw):
    result = []
    
    meta={'total': max_range, 'range_end': -1}
    
    while min(meta['total'], max_range) > meta['range_end']:
        kw.update({'range_start': meta['range_end']+1, 
                   'range_end': min(max_range, meta['total'], meta['range_end']+101)})
        
        page = requests.get(url % kw).json()
        result.extend(page['data'])
        
        meta = page['meta']['result']
        print("dl: %s %02.0d%%" % (url % kw, 100 * meta['range_end'] / meta['total']))
    return result

def yesno(_polls, max_polls=float("inf")):
    global g_votes
    _votes = defaultdict(lambda: defaultdict(int))
    _absent = defaultdict(lambda: defaultdict(int))
    _mandates = set()
    
    for ipoll, poll in enumerate(_polls):
        if ipoll >= max_polls:
            break

        if poll['id'] not in g_votes:
            g_votes[poll['id']] = from_url(awatch['votes'], poll=poll['id'])

        for vote in g_votes[poll['id']]:
            mandate = vote['mandate']['label']
            mandate += " (" + (vote['fraction']['label'] if vote['fraction'] else "?") + ")"
            mandate = re.sub(r" \(Bundestag [0-9]+ - [0-9]+\)", "", mandate)
            _mandates.add(mandate)
            
            if vote['vote'] in "yes,no":
                _votes[poll['label']][mandate] = 1 if vote['vote'] == "yes" else -1
            if vote['vote'] in "no_show,abstain":
                _absent[poll['label']][mandate] = 1 if vote['vote'] == "abstain" else -1
    
    _mandates = sorted(list(_mandates))
    return pd.DataFrame(data={p: [_votes[p][m] for m in _mandates] for p in _votes}, index=_mandates, dtype=float), \
           pd.DataFrame(data={p: [_absent[p][m] for m in _mandates] for p in _absent}, index=_mandates, dtype=float)

#### Receive serious data

In [4]:
polls = from_url(awatch['polls'], legislature=legis_id)

dl: https://www.abgeordnetenwatch.de/api/v2/polls?field_legislature=83&range_start=0&range_end=100 106%


In [5]:
_yesno, _absent = yesno(polls)

dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=999&range_start=0&range_end=100 16%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=999&range_start=101&range_end=201 32%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=999&range_start=202&range_end=302 48%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=999&range_start=303&range_end=403 65%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=999&range_start=404&range_end=504 81%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=999&range_start=505&range_end=605 97%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=999&range_start=606&range_end=619 100%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=998&range_start=0&range_end=100 16%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=998&range_start=101&range_end=201 32%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=998&range_start=202&range_end=302 48%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=998&range_start=30

dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=978&range_start=505&range_end=605 97%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=978&range_start=606&range_end=619 100%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=977&range_start=0&range_end=100 16%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=977&range_start=101&range_end=201 32%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=977&range_start=202&range_end=302 48%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=977&range_start=303&range_end=403 65%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=977&range_start=404&range_end=504 81%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=977&range_start=505&range_end=605 97%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=977&range_start=606&range_end=619 100%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=965&range_start=0&range_end=100 16%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=965&range_start=1

dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=929&range_start=303&range_end=403 65%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=929&range_start=404&range_end=504 81%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=929&range_start=505&range_end=605 97%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=929&range_start=606&range_end=619 100%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=928&range_start=0&range_end=100 16%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=928&range_start=101&range_end=201 32%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=928&range_start=202&range_end=302 48%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=928&range_start=303&range_end=403 65%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=928&range_start=404&range_end=504 81%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=928&range_start=505&range_end=605 97%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=928&range_start=

dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=905&range_start=202&range_end=302 48%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=905&range_start=303&range_end=403 65%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=905&range_start=404&range_end=504 81%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=905&range_start=505&range_end=605 97%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=905&range_start=606&range_end=619 100%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=903&range_start=0&range_end=100 16%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=903&range_start=101&range_end=201 32%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=903&range_start=202&range_end=302 48%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=903&range_start=303&range_end=403 65%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=903&range_start=404&range_end=504 81%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=903&range_start=

dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=871&range_start=0&range_end=100 16%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=871&range_start=101&range_end=201 32%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=871&range_start=202&range_end=302 48%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=871&range_start=303&range_end=403 65%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=871&range_start=404&range_end=504 81%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=871&range_start=505&range_end=605 97%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=871&range_start=606&range_end=620 100%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=870&range_start=0&range_end=100 16%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=870&range_start=101&range_end=201 32%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=870&range_start=202&range_end=302 48%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=870&range_start=30

dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=842&range_start=505&range_end=605 97%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=842&range_start=606&range_end=621 100%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=841&range_start=0&range_end=100 16%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=841&range_start=101&range_end=201 32%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=841&range_start=202&range_end=302 48%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=841&range_start=303&range_end=403 64%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=841&range_start=404&range_end=504 81%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=841&range_start=505&range_end=605 97%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=841&range_start=606&range_end=621 100%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=839&range_start=0&range_end=100 16%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=839&range_start=1

dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=807&range_start=303&range_end=403 64%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=807&range_start=404&range_end=504 81%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=807&range_start=505&range_end=605 97%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=807&range_start=606&range_end=621 100%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=806&range_start=0&range_end=100 16%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=806&range_start=101&range_end=201 32%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=806&range_start=202&range_end=302 48%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=806&range_start=303&range_end=403 64%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=806&range_start=404&range_end=504 81%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=806&range_start=505&range_end=605 97%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=806&range_start=

dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=734&range_start=101&range_end=201 32%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=734&range_start=202&range_end=302 48%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=734&range_start=303&range_end=403 64%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=734&range_start=404&range_end=504 81%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=734&range_start=505&range_end=605 97%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=734&range_start=606&range_end=621 100%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=733&range_start=0&range_end=100 16%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=733&range_start=101&range_end=201 32%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=733&range_start=202&range_end=302 48%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=733&range_start=303&range_end=403 64%
dl: https://www.abgeordnetenwatch.de/api/v2/votes?poll=733&range_start=

#### Render a dendroheatmap of all votes of all mandates and all polls (Bundestag 2017-2021)

In [6]:
#!pip install seaborn fastcluster

import seaborn

g = seaborn.clustermap(data=_yesno*-1,
                       figsize=(50,300),
                       tree_kws=dict(linewidths=2.5),
                       cmap='coolwarm',
                       center=0,
                       cbar_pos=None,
                       facecolor='w')
g.savefig(f"blau-pro--rot-contra-{legis_id}.jpg")
g

In [7]:
g = seaborn.clustermap(data=_absent*-1,
                       figsize=(50,300),
                       tree_kws=dict(linewidths=2.5),
                       cmap='coolwarm',
                       center=0,
                       cbar_pos=None,
                       facecolor='w')
g.savefig(f"blau-enthaltung--rot-abwesend-{legis_id}.jpg")
g